In [1]:
import yfinance as yf
import pandas as pd
from datetime import datetime, timedelta
import pandas_ta as ta
import os


# Specify the path to your CSV file
csv_file = 'C:\\Users\\prasa\\Downloads\\ind_stock.csv'

# Read the CSV file into a DataFrame
df = pd.read_csv(csv_file)

def get_stock_data(ticker, interval, start, end):
    stock = yf.Ticker(ticker)
    data = stock.history(interval=interval, start=start)
#     data = yf.download(ticker, period= interval, start=start)
    return data

def is_bullish_engulfing(data):
    bullish_engulfing = []
    for i in range(1, len(data)):
        prev_open = data['Open'].iloc[i-1]
        prev_close = data['Close'].iloc[i-1]
        curr_open = data['Open'].iloc[i]
        curr_close = data['Close'].iloc[i]
        
        if curr_open <= prev_close and curr_open < prev_open and curr_close > prev_open and curr_close > prev_close:
            bullish_engulfing.append(True)
        else:
            bullish_engulfing.append(False)
    # The first entry cannot be determined, so we prepend a False
    bullish_engulfing.insert(0, False)
    data['Bullish Engulfing'] = bullish_engulfing
    return data
def is_breaking_52_week_high(data):
    breaking_52_week_high = []
    for i in range(len(data)):
        current_high = data['High'].iloc[i]
        past_52_weeks = data['Close'].iloc[max(0, i-252):i]
        if not past_52_weeks.empty and current_high > past_52_weeks.max():
            breaking_52_week_high.append(True)
        else:
            breaking_52_week_high.append(False)
    data['Breaking 52-Week High'] = breaking_52_week_high
    return data

def is_bullish_thrusting(data):
    bullish_thrusting = []
    bullish_tweezer_bottom = []
    for i in range(1, len(data)):
        prev_open = data['Open'].iloc[i-1]
        prev_close = data['Close'].iloc[i-1]
        curr_open = data['Open'].iloc[i]
        curr_close = data['Close'].iloc[i]
        last_candle_movement = (((prev_close - prev_open) / prev_open) * 100)
        if last_candle_movement < 0 :
            if curr_open > prev_close  and curr_close > prev_open:
                bullish_thrusting.append(True)
            else:
                bullish_thrusting.append(False)
        else :
            bullish_thrusting.append(False)
            
        prev_open = data['Open'].iloc[i-1]
        prev_close = data['Close'].iloc[i-1]
        prev_low = data['Low'].iloc[i-1]
        curr_open = data['Open'].iloc[i]
        curr_close = data['Close'].iloc[i]
        curr_low = data['Low'].iloc[i]
        
        if prev_low == curr_low and prev_close < prev_open and curr_close > curr_open:
            bullish_tweezer_bottom.append(True)
        else:
            bullish_tweezer_bottom.append(False)
    # The first entry cannot be determined, so we prepend a False
    bullish_thrusting.insert(0, False)
    data['Bullish Thrusting'] = bullish_thrusting
    bullish_tweezer_bottom.insert(0, False)
    data['Bullish Tweezer Bottom'] = bullish_tweezer_bottom
    return data

def add_percentage_change(data):
    past5days_change = [None] * len(data)
    past10days_change = [None] * len(data)
    past15days_change = [None] * len(data)
    BE_condition = [False] * len(data)
    BT_condition = [False] * len(data)
    Max_gain_on  = [5] * len(data)
    Max_gain  = [None] * len(data)
    SL_Hit_on  = [None] * len(data)
    SL_rs = 1000
    Take_trade = [False] * len(data)
    for i in range(0, len(data)):
        if data['Bullish Thrusting'].iloc[i] == True or data['Bullish Engulfing'].iloc[i] == True or data['Bullish Tweezer Bottom'].iloc[i] == True :
            Take_trade[i] = True
    data['Take Trade'] = Take_trade
    for i in range(5, len(data)):
        open_5_days_ago = data['Open'].iloc[i-5]
        current_open = data['Open'].iloc[i]
        change_pct = ((current_open - open_5_days_ago) / open_5_days_ago) * 100
        past5days_change[i] = change_pct
    for i in range(10, len(data)):
        open_10_days_ago = data['Open'].iloc[i-10]
        current_open = data['Open'].iloc[i]
        change_pct = ((current_open - open_10_days_ago) / open_10_days_ago) * 100
        past10days_change[i] = change_pct
    for i in range(15, len(data)):
        open_15_days_ago = data['Open'].iloc[i-15]
        current_open = data['Open'].iloc[i]
        change_pct = ((current_open - open_15_days_ago) / open_15_days_ago) * 100
        past15days_change[i] = change_pct 
    for i in range(15, len(data)) :
        try :
            if (data['CRS SMA'].iloc[i] <= data['CRS'].iloc[i]) and int(data['ATR%'].iloc[i]) >= 3 and int(past5days_change[i]) <=0 and ((int(past5days_change[i]) >= int(past10days_change[i])) and  (int(past10days_change[i]) >= int(past15days_change[i]))) :
                BE_condition[i] = True
            if (data['CRS SMA'].iloc[i] <= data['CRS'].iloc[i]) and int(data['ATR%'].iloc[i]) >= 3 and int(past5days_change[i]) <=-4 and ((int(past5days_change[i]) >= int(past10days_change[i])) and  (int(past10days_change[i]) >= int(past15days_change[i]))) :
                BT_condition[i] = True
        except :
            pass
    data['-5 Day Change %'] = past5days_change
    data['-10 Day Change %'] = past10days_change
    data['-15 Day Change %'] = past15days_change
    data['BE Selection'] = BE_condition
    data['BT Selection'] = BT_condition
    exist_days = 5
    past_days = 15
    Quan = [None] * len(data)
    Fund = [None] * len(data)
    SL = [False] * len(data)
    for i in range(5, len(data)):
        sl = data['Low'].iloc[i]
        current_close = data['Close'].iloc[i]
        sl_price = max(current_close - sl,0.1)
        try :
            quantity = max(round(SL_rs/sl_price),1)
        except :
            quantity = 1
        trade_price = quantity * current_close
        Quan[i] = quantity
        Fund[i] = trade_price
        SL[i] = sl_price
    data[f'Quantity'] = Quan
    data[f'Fund'] = Fund
    data[f'SL'] = SL
            
    for j in range(5,exist_days+1):
        futuredays_change = [None] * len(data)
        futuredays2_change = [None] * len(data)
        futuredays_close = [None] * len(data)
        sl_hit = [False] * len(data)
        PNL = [None] * len(data)
        PNL2 = [None] * len(data)
        for i in range(0, len(data)-j):
            open_5_days_later = data['Close'].iloc[i+j]
            current_close = data['Close'].iloc[i]
            sl = data['Low'].iloc[i]
            change_pct = ((open_5_days_later - current_close ) / current_close) * 100
            futuredays_change[i] = change_pct 
            if Max_gain[i] == None :
                Max_gain[i] = change_pct
                Max_gain_on[i] = j
                
            if Max_gain[i] < change_pct:
                Max_gain[i] = change_pct
                Max_gain_on[i] = j
                
            sl_price = max(current_close - sl,0.1)
            try :
                quantity = max(round(SL_rs/sl_price),1)
            except :
                quantity = 1
            
            trade_price = quantity * current_close
            PNL[i] = (open_5_days_later - current_close ) * quantity
            Quan[i] = quantity
            Fund[i] = trade_price
            SL[i] = sl_price
        for i in range(0, len(data)-j):
            open_5_days_later = data['Close'].iloc[i+j]
            next_open = data['Open'].iloc[i+1]
            change_pct = ((open_5_days_later - next_open ) / next_open) * 100
            futuredays2_change[i] = change_pct
        for i in range(0, len(data)-j):
            open_5_days_later = data['Close'].iloc[i+j]
            futuredays_close[i] = open_5_days_later
            for k in range(1, j+1):
                sl = data['Low'].iloc[i]
                current_close = data['Close'].iloc[i]
                if sl >= data['Low'].iloc[i+k]:
                    sl_hit[i] = True
                    PNL[i] = -(SL[i] * Quan[i])
                    if SL_Hit_on[i] == None:
                        SL_Hit_on[i] = k
                
        data[f'cdc {j} Day After c %'] = futuredays_change
        data[f'cdc {j} Day After c PNL'] = PNL
        #data[f'ndo {j} Day After c %'] = futuredays2_change
        #data[f'{j}-Day After exit'] = futuredays_close
        data[f'SL Hit {j} Day'] = sl_hit
    data[f'Max_gain_on_day'] = Max_gain_on
    data[f'Max_gain'] = Max_gain
    data[f'SL_HIT_On'] = SL_Hit_on
    return data

def add_comparative_rsi(data, benchmark_data, length=100, lookbackMATrend=3):
    baseSymbol = data['Close']
    comparativeSymbol = benchmark_data['Close']
    
    crs = baseSymbol / comparativeSymbol
    crsSma = ta.sma(baseSymbol / comparativeSymbol, length)
    
    if crsSma is None:
        print("CRS SMA calculation returned None")
        return data
    
    if crsSma.isna().all():
        print("CRS SMA contains only NaN values")
        return data
    
    crsRising = crsSma > crsSma.shift(lookbackMATrend)
    crsFalling = crsSma < crsSma.shift(lookbackMATrend)
#     data['nifty close'] = comparativeSymbol
    data['CRS'] = crs
    data['CRS SMA'] = crsSma
    data['CRS Rising'] = crsRising
    data['CRS Falling'] = crsFalling
    
    return data

def add_atr_percentage(data):
    try :
        data['ATR%'] = round(((data['ATR'] / data['Close']) * 100), 2)
    except :
        data['ATR%'] = ((data['ATR'] / data['Close']) * 100)
    return data

combined_data = pd.DataFrame()
benchmark_ticker = '^NSEI'  # NIFTY50
end_date = datetime.now()
start_date = end_date - timedelta(days=5000)
interval = "1wk"
benchmark_data = get_stock_data(benchmark_ticker, interval, start_date.strftime('%Y-%m-%d'), end_date.strftime('%Y-%m-%d'))

for index, row in df.iterrows():
    company_name = row['Company Name']
    industry = row['Industry']
    symbol = row['Symbol']
    series = row['Series']
    isin_code = row['ISIN Code']
    if series == 'BE':
        continue
    print(company_name)
    end_date = datetime.now()
    start_date = end_date - timedelta(days=5000)
    start_date_str = start_date.strftime('%Y-%m-%d')
    end_date_str = end_date.strftime('%Y-%m-%d')
    data = get_stock_data(symbol+'.NS', interval, start=start_date_str, end=end_date_str)
    data['ATR'] = ta.atr(data['High'], data['Low'], data['Close'], length=22)
    save_dir = f'D:\\Program Files\\StockData\\Daily\\{symbol}\\'
    os.makedirs(save_dir, exist_ok=True)
    file_name = f"Data_{interval}_{start_date_str}_to_{end_date_str}.csv"
    file_path = os.path.join(save_dir, file_name)
    data = is_bullish_engulfing(data)
    data = is_bullish_thrusting(data)
    data = is_breaking_52_week_high(data)
    data = add_atr_percentage(data)
    data = add_comparative_rsi(data, benchmark_data)
    data = add_percentage_change(data)
    print(data)
    data['Company Name'] = company_name
    data['Industry'] = industry
    data['Symbol'] = symbol
    data['Series'] = series
    data['ISIN Code'] = isin_code
    data.to_csv(file_path)
    combined_data = pd.concat([combined_data, data])

save_dir = 'D:\\Program Files\\StockData\\Combined_daily_data\\'
os.makedirs(save_dir, exist_ok=True)
combined_file_path = os.path.join(save_dir, f'Data_LT_{interval}.csv')
# combined_data = combined_data.loc[combined_data['Breaking 52-Week High'] == True]
# combined_data = combined_data.loc[combined_data['Take Trade'] == True]
# combined_data = combined_data.loc[combined_data['BE Selection'] == True]
combined_data = combined_data.sort_index()
combined_data = combined_data.filter(like='2024-07', axis=0)
combined_data.to_csv(combined_file_path)


360 ONE WAM Ltd.
                                  Open         High         Low       Close  \
Date                                                                          
2019-09-16 00:00:00+05:30   250.634508   276.319366  250.634508  276.319366   
2019-09-23 00:00:00+05:30   290.135389   319.859405  263.280226  269.287170   
2019-09-30 00:00:00+05:30   259.241110   282.740683  243.032716  265.082336   
2019-10-07 00:00:00+05:30   267.164033   269.245735  238.206409  239.438858   
2019-10-14 00:00:00+05:30   238.216814   266.739437  224.742605  249.132874   
...                                ...          ...         ...         ...   
2024-06-10 00:00:00+05:30   800.000000   819.700012  778.000000  802.099976   
2024-06-17 00:00:00+05:30   802.099976   864.500000  787.150024  837.599976   
2024-06-24 00:00:00+05:30   837.500000  1065.000000  826.000000  980.150024   
2024-07-01 00:00:00+05:30   995.000000  1018.150024  920.200012  964.700012   
2024-07-08 00:00:00+05:30  1034.949

                                  Open         High          Low        Close  \
Date                                                                            
2010-11-01 00:00:00+05:30   740.815905   744.903170   730.895799   733.237488   
2010-11-08 00:00:00+05:30   736.558539   765.254528   717.442038   725.318542   
2010-11-15 00:00:00+05:30   735.366249   741.667428   706.499957   711.140686   
2010-11-22 00:00:00+05:30   715.270468   736.132537   638.634354   649.703979   
2010-11-29 00:00:00+05:30   659.837239   696.494860   621.604351   686.234131   
...                                ...          ...          ...          ...   
2024-06-10 00:00:00+05:30  8178.049805  9145.000000  7994.299805  9020.000000   
2024-06-17 00:00:00+05:30  9020.000000  9149.950195  8355.000000  8399.400391   
2024-06-24 00:00:00+05:30  8389.049805  8720.150391  8235.700195  8490.900391   
2024-07-01 00:00:00+05:30  8490.900391  8808.700195  8414.049805  8679.400391   
2024-07-08 00:00:00+05:30  8

                                  Open         High          Low        Close  \
Date                                                                            
2010-11-01 00:00:00+05:30   414.054403   414.054403   390.780768   398.719055   
2010-11-08 00:00:00+05:30   396.914853   423.977229   386.134995   399.711304   
2010-11-15 00:00:00+05:30   410.446126   410.446126   383.609264   391.773071   
2010-11-22 00:00:00+05:30   393.306617   419.466919   366.244235   372.919617   
2010-11-29 00:00:00+05:30   362.635938   396.914957   362.455511   383.203339   
...                                ...          ...          ...          ...   
2024-06-10 00:00:00+05:30  3733.000000  4005.000000  3708.050049  3976.800049   
2024-06-17 00:00:00+05:30  3976.800049  4339.700195  3965.199951  4250.299805   
2024-06-24 00:00:00+05:30  4250.299805  4336.899902  4051.100098  4178.549805   
2024-07-01 00:00:00+05:30  4222.850098  4327.200195  4171.000000  4262.350098   
2024-07-08 00:00:00+05:30  4

                                 Open        High         Low       Close  \
Date                                                                        
2017-07-10 00:00:00+05:30  266.983760  360.701523  264.696760  297.709259   
2017-07-17 00:00:00+05:30  293.334137  305.117226  279.587194  290.077637   
2017-07-24 00:00:00+05:30  291.594026  304.272027  283.390613  292.588379   
2017-07-31 00:00:00+05:30  293.334138  295.820020  269.345371  275.584930   
2017-08-07 00:00:00+05:30  273.447070  289.083276  246.723833  269.221069   
...                               ...         ...         ...         ...   
2024-06-10 00:00:00+05:30  668.143454  678.526998  646.976913  660.205994   
2024-06-17 00:00:00+05:30  660.206009  674.932722  648.973771  666.545959   
2024-06-24 00:00:00+05:30  659.207595  699.843350  637.491934  670.988953   
2024-07-01 00:00:00+05:30  670.988966  681.122966  660.755149  671.538086   
2024-07-08 00:00:00+05:30  666.895466  667.194980  623.563961  642.783569   

                                  Open         High          Low        Close  \
Date                                                                            
2018-10-08 00:00:00+05:30   750.000000   798.000000   710.049988   781.400024   
2018-10-15 00:00:00+05:30   758.099976   797.000000   732.000000   736.650024   
2018-10-22 00:00:00+05:30   750.000000   750.000000   612.250000   662.799988   
2018-10-29 00:00:00+05:30   655.049988   679.950012   622.000000   670.299988   
2018-11-05 00:00:00+05:30   656.000000   670.000000   638.700012   668.799988   
...                                ...          ...          ...          ...   
2024-06-10 00:00:00+05:30  1719.949951  1934.000000  1675.000000  1853.800049   
2024-06-17 00:00:00+05:30  1853.800049  1978.949951  1848.000000  1914.699951   
2024-06-24 00:00:00+05:30  1934.750000  1934.750000  1840.000000  1853.099976   
2024-07-01 00:00:00+05:30  1860.000000  1917.750000  1764.300049  1779.050049   
2024-07-08 00:00:00+05:30  1

...

                                 Open        High         Low       Close  \
Date                                                                        
2010-11-01 00:00:00+05:30  215.393264  215.882058  211.482957  213.438110   
2010-11-08 00:00:00+05:30  213.438122  223.213914  206.065544  210.668320   
2010-11-15 00:00:00+05:30  208.835355  213.478841  192.216502  194.334595   
2010-11-22 00:00:00+05:30  199.589101  201.218399  158.041982  169.610001   
2010-11-29 00:00:00+05:30  169.610008  187.328634  125.089422  130.506836   
...                               ...         ...         ...         ...   
2024-06-10 00:00:00+05:30  530.163158  552.013796  510.641250  533.235107   
2024-06-17 00:00:00+05:30  533.235136  544.433023  510.145798  511.334961   
2024-06-24 00:00:00+05:30  515.298827  564.549515  501.128121  544.086182   
2024-07-01 00:00:00+05:30  549.049988  620.299988  544.849976  616.400024   
2024-07-08 00:00:00+05:30  618.500000  670.950012  605.549988  658.450012   

Whirlpool of India Ltd.
                                  Open         High          Low        Close  \
Date                                                                            
2010-11-01 00:00:00+05:30   301.070116   301.070116   292.633887   295.510986   
2010-11-08 00:00:00+05:30   296.291177   320.770804   294.681965   298.485565   
2010-11-15 00:00:00+05:30   300.289873   307.214394   283.027368   284.977936   
2010-11-22 00:00:00+05:30   276.005311   302.240439   274.103496   280.540375   
2010-11-29 00:00:00+05:30   277.955898   297.364040   270.153627   284.246490   
...                                ...          ...          ...          ...   
2024-06-10 00:00:00+05:30  1640.000000  1837.800049  1630.000000  1784.900024   
2024-06-17 00:00:00+05:30  1784.900024  1856.949951  1757.400024  1847.199951   
2024-06-24 00:00:00+05:30  1854.800049  2199.000000  1815.849976  1998.349976   
2024-07-01 00:00:00+05:30  1998.349976  2045.750000  1921.000000  2022.349976   
2024

                                Open       High        Low      Close  \
Date                                                                    
2010-11-01 00:00:00+05:30  68.475277  68.475277  66.861983  67.112938   
2010-11-08 00:00:00+05:30  66.691691  67.399740  61.860772  62.165508   
2010-11-15 00:00:00+05:30  62.470239  64.549592  55.335908  57.684143   
2010-11-22 00:00:00+05:30  57.719988  59.154024  51.983839  55.049091   
2010-11-29 00:00:00+05:30  55.515163  61.260275  54.448599  59.145069   
...                              ...        ...        ...        ...   
2024-06-10 00:00:00+05:30  23.400000  24.500000  23.209999  23.809999   
2024-06-17 00:00:00+05:30  23.809999  24.650000  23.500000  23.840000   
2024-06-24 00:00:00+05:30  23.889999  24.450001  23.320000  23.690001   
2024-07-01 00:00:00+05:30  23.780001  27.040001  23.610001  26.639999   
2024-07-08 00:00:00+05:30  26.950001  27.440001  24.600000  25.600000   

                               Volume  Dividends  

                                 Open        High         Low       Close  \
Date                                                                        
2010-11-01 00:00:00+05:30  135.836830  135.904779  133.730308  133.979462   
2010-11-08 00:00:00+05:30  134.115336  140.434912  128.837704  130.060852   
2010-11-15 00:00:00+05:30  130.468592  133.050788  120.049225  129.064240   
2010-11-22 00:00:00+05:30  131.329268  132.235299  124.216928  128.158157   
2010-11-29 00:00:00+05:30  125.893110  138.124539  125.122992  134.500412   
...                               ...         ...         ...         ...   
2024-06-10 00:00:00+05:30  157.000000  168.699997  154.000000  163.979996   
2024-06-17 00:00:00+05:30  163.979996  165.089996  153.619995  154.240005   
2024-06-24 00:00:00+05:30  154.100006  160.250000  148.100006  151.789993   
2024-07-01 00:00:00+05:30  152.000000  156.289993  148.399994  151.100006   
2024-07-08 00:00:00+05:30  151.100006  159.389999  145.899994  155.500000   

                                  Open         High          Low        Close  \
Date                                                                            
2010-11-01 00:00:00+05:30   125.094397   127.700531   125.094397   125.285515   
2010-11-08 00:00:00+05:30   127.700537   136.387649   125.459261   134.076874   
2010-11-15 00:00:00+05:30   134.684954   143.337322   130.306657   136.153091   
2010-11-22 00:00:00+05:30   134.823989   138.125095   125.285543   130.410934   
2010-11-29 00:00:00+05:30   129.785443   136.387653   127.561544   134.346176   
...                                ...          ...          ...          ...   
2024-06-10 00:00:00+05:30  1062.900024  1111.800049  1059.000000  1109.550049   
2024-06-17 00:00:00+05:30  1109.550049  1109.550049  1050.000000  1085.050049   
2024-06-24 00:00:00+05:30  1080.099976  1091.300049  1050.050049  1073.949951   
2024-07-01 00:00:00+05:30  1093.349976  1166.849976  1059.000000  1162.449951   
2024-07-08 00:00:00+05:30  1